In [1]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import networkx as nx
import csv

hist = []
files = ['../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv'
         ]

# preenche as listas iniciais
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        reader = csv.DictReader(csvfile, delimiter=';')
        for row in reader:
            hist.append(row)
print(len(hist))
print(hist[0])

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv
76844
{'ID_ANONIMO': '13236', 'CR': '0,6826', 'PERIODO': '1', 'INGRESSO': '12/07/07', 'CODIGO': 'IF68E', 'ANO': '2012', 'NOTA': '8,2', 'CH': '60', 'SITUACAOALUNO': 'Formado'}


In [2]:
# função para verificar se um aluno teve seu ingresso antes ou depois de 2014
def beforeClasses(date):
    year = date.split('/')[2]
    if (int(year) < 14):
        return True
    return False

In [3]:
# Remove todos os alunos que ingressaram antes de 2014 
for i in range(len(hist)):
    if (i == len(hist)):
        break
    if (beforeClasses(hist[i]['INGRESSO'].split(" ")[0])):
        hist.pop(i)
        i = 0

# Remove todos dados de reprovações (matérias repetidas)
for i in range(len(hist)):
    for j in range(i, len(hist)):
        if (j == len(hist)):
            break
        if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
            break
        if (j < len(hist) and (i != j and (hist[i]["ID_ANONIMO"] == hist[j]["ID_ANONIMO"] and hist[i]["CODIGO"] == hist[j]["CODIGO"]))):
            hist.pop(j)
            j -= 5
len(hist)

# TODO: caso o aluno tenha reprovado em uma matéria, deve ser removido também. 
# Uma reprovação não conta para o sistema de recomendação

49188

In [4]:
G = nx.Graph()

# Adiciona todos os nós, que são os alunos
# Sem colocar nenhum aluno pré-2014
for line in hist:
    if (not beforeClasses(line['INGRESSO'].split(" ")[0])):
        if not G.has_node(line["ID_ANONIMO"]):
            G.add_node(line["ID_ANONIMO"])
G.nodes()

NodeView(('90729', '113853', '118844', '123664', '123676', '123677', '123686', '123688', '123736', '129034', '131006', '131014', '136341', '136730', '136731', '136736', '145077', '150873', '150878', '150887', '150892', '151217', '156158', '158257', '159067', '160836', '160839', '160852', '160855', '161216', '161223', '161226', '161228', '165431', '165432', '165685', '165892', '165894', '165895', '166050', '169043', '171740', '171745', '171746', '171749', '171750', '171751', '171754', '171755', '172044', '172045', '172046', '172207', '172208', '172248', '172307', '172974', '175962', '179385', '179393', '179397', '179408', '179624', '179652', '179819', '179822', '179823', '179944', '180984', '182856', '182913', '183413', '183414', '186021', '186024', '186036', '189048', '190493', '190494', '190495', '190499', '190508', '190615', '191284', '198372', '198543', '202261', '11357', '104342', '104372', '104768', '110307', '113861', '118817', '123657', '123682', '124800', '126813', '130359', '1

In [5]:
print(G.number_of_nodes())

901


In [6]:
# Verifica quais são as matérias obrigatórias, que não serão levadas em conta
optional = []
with open('../texts/optativas.txt', 'r') as f:   
    lines = f.readlines()
    for l in lines:
        optional.append(l.split(" ")[0])

print(optional)

['CSH30', 'CSV30', 'CSH42', 'CSI53', 'CSV40', 'CSR44', 'CSR41', 'CSR42', 'MA70C', 'CSB51', 'ED70T', 'CSB41', 'CSI41', 'DI84D', 'CSV45', 'CSR43', 'CSM44', 'CSM41', 'CSM43', 'ES70J', 'ES70B', 'CSM40', 'CSB53', 'ES70N', 'GE70F', 'CSA44', 'CSB54', 'CSH44', 'EEY41', 'ED70U', 'CSH43', 'CSE40', 'CSM30', 'CSI56', 'CSA45', 'FI70B', 'FI70D', 'CSA42', 'EL64B', 'CSV52', 'CSB52', 'CSD41', 'FI70A', 'CSD40', 'CSR53', 'CSG42', 'CSI58', 'CSI57', 'CSG48', 'CSV41', 'CSI51', 'CSW45', 'CSE43', 'CSI55', 'FCH7HB', 'CSR47', 'EEY44', 'CSH45', 'CSA41', 'EEC41', 'EL6CB', 'EEY43', 'CSR48', 'EEY42', 'EL6AE', 'CSH41', 'CSD52', 'EEY51', 'EEL51', 'CSI54', 'CSA43', 'CSW47', 'CSI31', 'IF6BV', 'CSR45', 'CSG44', 'FI70E', 'EL75H']


In [7]:
# Adiciona as arestas
with open('all_edges.txt', 'w') as f:
    for i in range(len(hist)):
        # o estudante deve estar no grafo
        if G.has_node(hist[i]["ID_ANONIMO"]):
            # a disciplina não pode ser obrigatória
            if (hist[i]["CODIGO"] in optional):
                for j in range(i, len(hist)):
                    # o estudante deve estar no grafo
                    if G.has_node(hist[j]["ID_ANONIMO"]):
                        # a disciplina não pode ser obrigatória
                        if (hist[j]["CODIGO"] in optional):
                            # os alunos deve ser diferentes
                            if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
                                # as disciplinas que eram obrigatorias antes de 2017 n contam
                                if (line['CODIGO'] != 'ES70N' or int(line['ANO']) > 2017):
                                    if (line['CODIGO'] != 'FI70D' or int(line['ANO']) > 2017):
                                       if (line['CODIGO'] != 'FI70A' or int(line['ANO']) > 2017) and \
                                           (line['CODIGO'] != 'GE70F' or int(line['ANO']) > 2017):
                                            # as matérias devem ser as mesmas
                                            if (hist[i]["CODIGO"] == hist[j]["CODIGO"]):
                                                f.write(hist[i]["ID_ANONIMO"] + " - " + hist[j]["ID_ANONIMO"] + " : " + hist[j]["CODIGO"] + "\n")
                                                if (G.has_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"])):
                                                    G[hist[i]["ID_ANONIMO"]][hist[j]["ID_ANONIMO"]]['weight'] += 1
                                                else:
                                                    G.add_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"], weight = 1) 

In [8]:
# Remover as arestas com peso pequeno
edges_remove = []
for u, v, a in G.edges(data=True):
    if a["weight"] < 0:
        edges_remove.append([u, v])
G.remove_edges_from(edges_remove)

In [9]:
print(G.number_of_edges())

17852


In [10]:
# ordena os vértices por grau, para verificar os alunos com maior n de matérias em comum
degrees = sorted(G.degree, key=lambda x: x[1], reverse=True)
remove = [node for node, degree in dict(G.degree()).items() if degree == 0]
G.remove_nodes_from(remove)
G.number_of_nodes()

260

In [11]:
with open('node_degree_all.txt', 'w') as f:
    for degree in degrees:
        f.write(str(degree) + "\n")

In [12]:
# Escreve o arquivo gexf para visualização de grafos
nx.write_gexf(G, "grafo_caminho.gexf")

In [13]:
# ordena as arestas por peso, buscando assim quais os estudantes mais relacionadas
edges = sorted(G.edges(data=True), key=lambda edge: edge[2].get('weight', 1))
with open('edge_weights.txt', 'w') as f1:
    for edge in edges:
        f1.write(str(edge) + "\n")


In [14]:
import leidenalg as la
import igraph as ig
# Separa o grafo em comunidades
# O alg usado para isso é o Leinden, com a biblioteca LeidenAlg
# para isso, é preciso transformar o grafo do networkX para Igraph
H = ig.Graph.from_networkx(G)
H.is_weighted()

True

In [15]:
ws = []
for e in H.es():
  ws.append(e['weight'])

In [17]:
ig.plot(H)

In [76]:
# Agora roda a partição
# Todos os algoritmos utilizados possuem a opção de utilizar arestas com ou sem peso
#   no nosso caso, sempre serão usadas arestas com peso

# Algoritmo de Leiden 
#partition = la.find_partition(H, la.ModularityVertexPartition, weights=H.es()[:]["weight"], n_iterations=50)

# Algoritmo de Infomap Martin Rosvall e Carl T. Bergstrom
# Este algoritmo também aceita vértices com peso, talvez possa ser interessante utilizando algum atributo para os alunos
# Não devide em nenhuma comunidade :(
#partition = H.community_infomap(edge_weights='weight')

# Algoritmo de propagação de labels (??) de Raghavan
# Não divide em nenhuma comunidade
#partition = H.community_label_propagation(weights='weight')

# Algoritmo de Newman
# Em média, divide em 2 comunidades.
# Engraçado que sem colocar pesos ele separa em 3
#partition = H.community_leading_eigenvector(weights='weight')

# Algoritmo de Leiden implementado no Igraph
# Separou em muitas comunidades wtf
# Verificar depois 
partition = H.community_leiden(weights='weight')

# Algoritmo de multilevel de Blondel
# separa de 3 a 4 comunidades
#partition = H.community_multilevel(weights='weight')

ig.plot(partition)



In [75]:
com_0 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 0]
com_1 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 1]
com_2 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 2]
com_3 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 3]

comunidades = []
for y in range(0,3):
    comunidades.append([H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == y])

# print(comunidades)
    
# Pandas
import pandas as pd
# preenche as listas iniciais
dados = []
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        dados.append(pd.read_csv(csvfile, delimiter=';'))

dados = pd.concat(dados)

dados_filtrados = dados[dados.CODIGO.apply(lambda a: a in optional)]
dados_filtrados = dados_filtrados[[int(x[3].split('/')[2].split(' ')[0]) >= 14 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[float(str(x[7]).replace(',','.')) >= 6 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'ES70N' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'FI70D' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'FI70A' or x[5] > 2017 for x in dados_filtrados.values]]
dados_filtrados = dados_filtrados[[x[4] != 'GE70F' or x[5] > 2017 for x in dados_filtrados.values]]
#dados_filtrados

from collections import Counter

disciplinas_comunidades = []

# Pega as disciplinas de cada comunidade
for idx, comunidade in enumerate(comunidades):
    disciplinas_comunidades.append(pd.DataFrame())
    for id in comunidade:
        disciplinas_comunidades[idx] = pd.concat([disciplinas_comunidades[idx],
                   dados_filtrados[dados_filtrados.ID_ANONIMO.apply(lambda a: a == int(id))]
                  ])
        pass

# Pega as disciplinas mais populares em cada comunidade
for idx, comunidade in enumerate(disciplinas_comunidades):
    print("Comunidade " + str(idx) + ": " + str(Counter(comunidade.CODIGO).most_common(8)))

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv
Comunidade 0: [('CSH30', 122), ('CSH42', 43), ('CSV30', 36), ('MA70C', 29), ('FI70D', 20), ('CSR41', 16), ('ES70N', 16), ('FI70A', 16)]
Comunidade 1: [('CSD40', 2), ('ES70J', 2), ('ES70B', 2), ('CSR45', 1), ('CSB54', 1), ('CSI31', 1), ('ES70N', 1), ('CSI53', 1)]
Comunidade 2: [('MA70C', 2), ('EL64B', 1)]


In [ ]:
# https://stackoverflow.com/questions/43541376/how-to-draw-communities-with-networkx

# Criar função para plotar gráficos 

In [ ]:
# Algoritmo de Louvain, utilizando diretamente o grafo do networkX
# Como o algoritmo de Leiden é baseado no Louvain, é esperado que o resultado seja parecido
# E parece ser.
louvain_c = nx.community.louvain_communities(G)
print(len(louvain_c), louvain_c)

4 [{'160791', '156158', '175469', '212672', '186026', '213594', '136734', '175962', '179385', '194218', '202688', '193634', '198537', '182913', '180984', '229544', '213600', '179393', '198543', '172248', '136716', '176199', '186031', '130359', '208652', '179405', '177422', '190494', '161257', '193633', '198718', '208880', '212651', '183413', '104372', '150878', '190499', '136720', '202455', '183016', '171741', '157060', '150892', '198372', '212674', '179821'}, {'161226', '165685', '175798', '172973', '165686', '171753', '179823', '161840', '165892', '145760', '165564', '172409', '131755', '161104', '165898', '172047', '161839', '125585', '165565', '172046', '153843', '159067', '123664', '51969', '155125', '160852', '156565', '179645', '165431', '90327', '165894', '152094', '166078', '160851', '172306', '169044', '172045', '172307', '160839', '160843', '165430', '113582', '161222', '224204', '160847', '219036', '191284', '161072', '160837', '167374', '172038', '172975', '161223', '90293

In [ ]:
# Não entendi a diferença entre esse e o anterior
# Mas em tese esse cara deveria retornar um iterable e retorna um "generator" ?????
#louvain_p = nx.community.louvain_partitions(G)
#print(len(louvain_p), louvain_p)